Next cell is only required for Google Colab, if you don't use it, please skip the next cell

In [0]:
!pip install pytorch-lightning

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 801.6/801.6 kB 10.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 840.4/840.4 kB 52.2 MB/s eta 0:00:00


In [ ]:
import torch
import numpy as np
import cv2 as cv
import pytorch_lightning as pl
from torch import nn
import albumentations as A
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from tqdm import tqdm
import itertools
from pytorch_lightning.callbacks import ModelCheckpoint
from pytorch_lightning.callbacks.early_stopping import EarlyStopping
import pandas as pd

In [ ]:
if torch.cuda.is_available():
  device = torch.device("cuda")
  accelerator="gpu"
else:
  device = torch.device("cpu")
  accelerator="cpu"

The next cell is required only if you use Google Colab, otherwise skip it:

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
class BasicMobileNetBlock(nn.Module):
  def __init__(self, in_dim, out_dim, leaky_relu_coef=0, dropout=0.3, kernel_size=3):
    super().__init__()
    self.spatial_convolve = nn.Conv2d(
        in_dim,
        in_dim,
        kernel_size,
        padding=kernel_size // 2,
        padding_mode="reflect",
        groups=in_dim,
        )
    self.depthwise_convolve = nn.Conv2d(
        in_dim,
        out_dim,
        kernel_size=1,
    )
    if leaky_relu_coef == 0:
      self.ReLU = nn.ReLU()
    else:
      self.ReLU = nn.LeakyReLU(leaky_relu_coef)
    self.batch_norm = nn.BatchNorm2d(out_dim)
    self.dropout = nn.Dropout2d(p=dropout)

  def forward(self, X):
    _X = self.spatial_convolve(X)
    _X = self.depthwise_convolve(X)
    _X = self.ReLU(_X)
    _X = self.batch_norm(_X)
    return self.dropout(_X)

In [ ]:
class MySegmentationNet(nn.Module):
  def __init__(self, block_amount=2, leaky_relu_coef=0, dropout=0.3, kernel_size=3):
    super().__init__()
    self.in_layer = BasicMobileNetBlock(3, 64, leaky_relu_coef=leaky_relu_coef, dropout=dropout, kernel_size=kernel_size)
    self.basic_layers = nn.Sequential()
    for i in range(block_amount):
      self.basic_layers.append(BasicMobileNetBlock(64, 64, leaky_relu_coef=leaky_relu_coef, dropout=dropout, kernel_size=kernel_size))
    self.out_layer = nn.Conv2d(64, 3, 1)

  def forward(self, X):
    _X = self.in_layer(X)
    _X = self.basic_layers(_X)
    return self.out_layer(_X)

In [ ]:
class Recall(nn.Module):
  def __init__(self, target):
    super().__init__()
    self.target = target

  def forward(self, gt, pred):
    gt_positive = gt == self.target
    TP = (pred[gt_positive] == self.target).sum()
    FN = (~(pred[gt_positive] == self.target)).sum()
    return TP / (TP + FN)

In [ ]:
class Precision(nn.Module):
  def __init__(self, target):
    super().__init__()
    self.target = target

  def forward(self, gt, pred):
    gt_positive = gt == self.target
    TP = (pred[gt_positive] == self.target).sum()
    FP = (pred[~gt_positive] == self.target).sum()
    return TP / (TP + FP)

In [ ]:
class MyTrainingModule(pl.LightningModule):
    def __init__(
        self,
        opt='adam',
        white_weight=5.0,
        yellow_weight=5.0,
        amount_of_hidden_layers=2,
        kernel_size=5,
        leaky_relu_coef=0,
        dropout=0.3
        ):
        super().__init__()
        self.opt = opt
        self.amount_of_hidden_layers = amount_of_hidden_layers
        self.kernel_size = kernel_size
        self.leaky_relu_coef = leaky_relu_coef
        self.dropout = dropout

        self.model = MySegmentationNet(leaky_relu_coef=leaky_relu_coef, kernel_size=kernel_size, dropout=dropout, block_amount=amount_of_hidden_layers)
        self.loss = nn.CrossEntropyLoss(weight=torch.tensor([1.0,white_weight,yellow_weight]))
        self.val_recal_yellow = Recall(2)
        self.val_precision_yellow = Precision(2)
        self.val_recal_white = Recall(1)
        self.val_precision_white = Precision(1)


    def forward(self, X):
      return self.model(X)

    def training_step(self, batch, batch_idx):
        x, y = batch

        y_pred = self.model(x)
        loss = self.loss(y_pred, y)

        metrics = {"train_loss": loss}
        self.log_dict(metrics, prog_bar=True, on_step=True, on_epoch=True, logger=True)

        return loss

    def configure_optimizers(self):
        if self.opt == "adam":
          optimizer = torch.optim.Adam(self.parameters(), lr=1e-3, weight_decay=5e-4)
        else:
          optimizer = torch.optim.SGD(self.parameters(), lr=1e-3, momentum=0.9)

        lr_scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
            optimizer,
            mode="min",
            factor=0.1,
            patience=2,
            verbose=True,
        )
        lr_dict = {
            "scheduler": lr_scheduler,
            "interval": "epoch",
            "frequency": 1,
            "monitor": "val_loss",
        }

        return [optimizer], [lr_dict]

    def validation_step(self, batch, batch_idx):
        x, y = batch

        y_pred = self.model(x)

        y_pred_label = torch.argmax(y_pred, dim=1)
        y_label = y

        loss = self.loss(y_pred, y)

        yellow_recal = self.val_recal_yellow(y_label, y_pred_label)
        yellow_precision = self.val_precision_yellow(y_label, y_pred_label)
        white_recal = self.val_recal_white(y_label, y_pred_label)
        white_precision = self.val_precision_white(y_label, y_pred_label)

        metrics = {
            "val_loss": loss,
            "yellow_recal": yellow_recal,
            "yellow_precision": yellow_precision,
            "white_recal" : white_recal,
            "white_precision" : white_precision,
        }
        self.log_dict(metrics, prog_bar=True, on_step=True, on_epoch=True, logger=True)

        return metrics

If you use Windows or MacOS two cells below probably wouldn't work. To fix this download dataset from the link to any folder you like and unzip it.
If you use Colab or Linux, these two cells will work.

In [ ]:
!wget https://github.com/SPGC/DuckiebotDataset/archive/refs/heads/master.zip

--2024-03-13 11:41:09--  https://github.com/SPGC/DuckiebotDataset/archive/refs/heads/master.zip
Resolving github.com (github.com)... 20.27.177.113
Connecting to github.com (github.com)|20.27.177.113|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://codeload.github.com/SPGC/DuckiebotDataset/zip/refs/heads/master [following]
--2024-03-13 11:41:10--  https://codeload.github.com/SPGC/DuckiebotDataset/zip/refs/heads/master
Resolving codeload.github.com (codeload.github.com)... 20.27.177.114
Connecting to codeload.github.com (codeload.github.com)|20.27.177.114|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/zip]
Saving to: ‘master.zip’

master.zip              [       <=>          ]   1.62G  23.9MB/s    in 74s     

2024-03-13 11:42:24 (22.4 MB/s) - ‘master.zip’ saved [1737430044]


In [ ]:
!unzip master.zip

Выходные данные были обрезаны до нескольких последних строк (5000).
  inflating: DuckiebotDataset-master/dataset/labels/3468.png  
  inflating: DuckiebotDataset-master/dataset/labels/3469.png  
  inflating: DuckiebotDataset-master/dataset/labels/3470.png  
  inflating: DuckiebotDataset-master/dataset/labels/3471.png  
  inflating: DuckiebotDataset-master/dataset/labels/3472.png  
  inflating: DuckiebotDataset-master/dataset/labels/3473.png  
  inflating: DuckiebotDataset-master/dataset/labels/3474.png  
  inflating: DuckiebotDataset-master/dataset/labels/3475.png  
  inflating: DuckiebotDataset-master/dataset/labels/3476.png  
  inflating: DuckiebotDataset-master/dataset/labels/3477.png  
  inflating: DuckiebotDataset-master/dataset/labels/3478.png  
  inflating: DuckiebotDataset-master/dataset/labels/3479.png  
  inflating: DuckiebotDataset-master/dataset/labels/3480.png  
  inflating: DuckiebotDataset-master/dataset/labels/3481.png  
  inflating: DuckiebotDataset-master/dataset/label

Change these paths to the paths where you've unzipped the archive from previous step. If you use google colab this will work from the scratch

In [ ]:
data_path = "/content/DuckiebotDataset-master/dataset/data/"
label_path = "/content/DuckiebotDataset-master/dataset/labels/"

In [ ]:
import os
import random
TRAIN_PARTITION = 0.7
VAL_PARTITION = 0.1
class RoadDataset(Dataset):
  def __init__(
      self,
      data_path,
      labels_path,
      dataset_type="train",
      augmentations=None,
      shuffle_seed=239,
  ):
    self.data_path = data_path
    self.labels_path = labels_path
    self.dataset_type = dataset_type
    self.augmentations = augmentations
    self.class_amount = 3
    random.seed(shuffle_seed)
    data_names = os.listdir(data_path)
    random.shuffle(data_names)
    if self.dataset_type == "train":
      self.data_names = data_names[:int(len(data_names) * TRAIN_PARTITION)]
    elif self.dataset_type == "val":
      self.data_names = data_names[int(len(data_names) * TRAIN_PARTITION):int(len(data_names) * (VAL_PARTITION + TRAIN_PARTITION))]
    elif self.dataset_type == "test":
      self.data_names = data_names[int(len(data_names) * (VAL_PARTITION + TRAIN_PARTITION)):]
    else:
      raise Exception("Unknown dataset type")


  def __len__(self):
    return len(self.data_names)

  def __getitem__(self, index):
    img_name = self.data_names[index]
    img_path = self.data_path + img_name
    labels_path = self.labels_path + img_name
    image = cv.cvtColor(cv.imread(img_path), cv.COLOR_BGR2RGB).astype(np.uint8)
    labels = (cv.cvtColor(cv.imread(labels_path), cv.COLOR_BGR2RGB).astype(np.uint8)//255).sum(axis=-1)
    labels[labels==3]=1


    if self.augmentations:
      transformed = self.augmentations(image=image)
      image = transformed["image"]

    x = torch.from_numpy(image.astype(np.float32) / 255).permute(2, 0, 1)
    labels_tensor = torch.from_numpy(labels.astype(np.int64))

    return x, labels_tensor

In [ ]:
augmentations = A.Compose(
    [
        A.OneOf(
            [
              A.augmentations.transforms.RandomBrightnessContrast (brightness_limit=0.3, contrast_limit=0.2, brightness_by_max=True, always_apply=False, p=0.5),
              A.augmentations.transforms.RandomToneCurve (scale=0.5, always_apply=False, p=0.5)
            ],
            p=0.5
        ),
        A.augmentations.transforms.HueSaturationValue(always_apply=False, p=0.5),
        A.augmentations.transforms.RGBShift (r_shift_limit=20, g_shift_limit=20, b_shift_limit=20, always_apply=False, p=0.5)
    ]
)

In [ ]:
ds_train = RoadDataset(
    dataset_type="train",
    data_path=data_path,
    labels_path=label_path,
    augmentations=augmentations
    )
ds_val = RoadDataset(
    dataset_type="val",
    data_path=data_path,
    labels_path=label_path,
    augmentations=None
    )
ds_test = RoadDataset(
    dataset_type="test",
    data_path=data_path,
    labels_path=label_path,
    augmentations=None
    )

dl_train = DataLoader(ds_train, batch_size=32, shuffle=True, num_workers=os.cpu_count())
dl_val = DataLoader(ds_val, batch_size=32, shuffle=False, num_workers=os.cpu_count())
dl_test = DataLoader(ds_test, batch_size=32, shuffle=False, num_workers=os.cpu_count())

In [ ]:
ds_val.__len__()

847

These two cells sometimes doesn't work in colab. You can try uncomment them, but if something crashes, you have to commnet them back and restart the notebook|

In [ ]:
# %load_ext tensorboard

In [ ]:
# %tensorboard --logdir lightning_logs

Next cell is cell with adjusting hyperparameters. Cell with real training is after this one

In [ ]:
# Adjusting hyperparameters
class MyTrainingModuleKernel5(MyTrainingModule):
  def __init__(self,
               opt='adam',
               white_weight=5.0,
               yellow_weight=5.0,
               amount_of_hidden_layers=2,
               kernel_size=5,
               leaky_relu_coef=0,
               dropout=0.3):
    super().__init__(
        opt,
        white_weight,
        yellow_weight,
        amount_of_hidden_layers,
        kernel_size,
        leaky_relu_coef,
        dropout
    )
    self.opt = opt
    self.amount_of_hidden_layers = amount_of_hidden_layers
    self.kernel_size = kernel_size
    self.leaky_relu_coef = leaky_relu_coef
    self.dropout = dropout

    self.model = MySegmentationNet(leaky_relu_coef=leaky_relu_coef, kernel_size=kernel_size, dropout=dropout, block_amount=amount_of_hidden_layers)

class MyTrainingModuleKernel3(MyTrainingModule):
  def __init__(self,
               opt='adam',
               white_weight=5.0,
               yellow_weight=5.0,
               amount_of_hidden_layers=2,
               kernel_size=3,
               leaky_relu_coef=0,
               dropout=0.3):
    super().__init__(
        opt,
        white_weight,
        yellow_weight,
        amount_of_hidden_layers,
        kernel_size,
        leaky_relu_coef,
        dropout
    )
    self.opt = opt
    self.amount_of_hidden_layers = amount_of_hidden_layers
    self.kernel_size = kernel_size
    self.leaky_relu_coef = leaky_relu_coef
    self.dropout = dropout

    self.model = MySegmentationNet(leaky_relu_coef=leaky_relu_coef, kernel_size=kernel_size, dropout=dropout, block_amount=amount_of_hidden_layers)


kernel_size=[3, 5]
optimizer = ["adam", "sgd"]
yellow_weights = [5.0, 7.0, 10.0]
weight_weight = [5.0, 3.0, 2.0]
stats = {
    "params" : [],
    "val_loss" : [],
    "yellow_recal" : [],
    "white_recal" : [],
    "yellow_precision" : [],
    "white_precision" : [],
}
stats_dir = "/content/drive/MyDrive/Colab Notebooks/DuckieBot/stats/" # Dir to save statistics, you have to change it even if you use colab
checkpoints_dir = "/content/checkpoints/" # If you use Colab, you can leave this path as it is, otherwise change it, because usually you don't have permissions to create dirs in the root

all_combinations = list(itertools.product(optimizer, kernel_size, yellow_weights, weight_weight))

for i, combination in enumerate(all_combinations):
  if os.path.exists(checkpoints_dir):
    items = os.listdir(checkpoints_dir)
    for item in items:
      os.remove(checkpoints_dir + item)
    os.rmdir(checkpoints_dir)

  FaceModuleCheckpoint = ModelCheckpoint(
      dirpath=checkpoints_dir,
      filename="{epoch}-{val_loss:.3f}",
      save_top_k=2,
      mode="min",
      monitor="val_loss",
      every_n_epochs=1,
      save_last=True
  )

  MyEarlyStopping = EarlyStopping(monitor="val_loss", mode="min", patience=5, verbose=True)

  trainer = pl.Trainer(
      max_epochs=30,
      accelerator="gpu",
      devices=1,
      callbacks=[MyEarlyStopping, FaceModuleCheckpoint],
      log_every_n_steps=50,
  )

  training_module = MyTrainingModule(
      opt=combination[0],
      white_weight=combination[3],
      yellow_weight=combination[2],
      kernel_size=combination[1],
  )

  trainer.fit(training_module, dl_train, dl_val)
  checkpoints = os.listdir(checkpoints_dir)
  min_loss = 1
  weights = ""
  for checkpoint in checkpoints:
    if len(checkpoint.split(".")) < 3:
      continue
    score = float(".".join(checkpoint.split("-")[1].split("=")[1].split(".")[:-1]))
    if score < min_loss:
      min_loss = score
      weights = checkpoints_dir + checkpoint
  params = f"Optimizer: {combination[0]}, kernel_size: {combination[1]}, yellow_weights: {combination[2]}, wight_weights: {combination[3]}"

  if combination[1] == 5:
    test = MyTrainingModuleKernel5.load_from_checkpoint(weights)
  else:
    test = MyTrainingModuleKernel3.load_from_checkpoint(weights)
  result = {}
  counter = 0
  model = test.model
  model.eval()
  with torch.no_grad():
    for data, labels in dl_test:
      counter += 1
      data = data.to(device)
      labels = labels.to(device)

      x, y = data, labels

      y_pred = model(x)

      y_pred_label = torch.argmax(y_pred, dim=1)
      y_label = y

      loss = test.loss(y_pred, y).item()

      yellow_recal = test.val_recal_yellow(y_label, y_pred_label).item()
      yellow_precision = test.val_precision_yellow(y_label, y_pred_label).item()
      white_recal = test.val_recal_white(y_label, y_pred_label).item()
      white_precision = test.val_precision_white(y_label, y_pred_label).item()

      buf = {
          "val_loss": loss,
          "yellow_recal": yellow_recal,
          "yellow_precision": yellow_precision,
          "white_recal" : white_recal,
          "white_precision" : white_precision,
      }
      del x
      del y
      del y_pred_label
      del y_pred
      del y_label
      if len(result) == 0:
        result = buf
      else:
        for name in result.keys():
          result[name] += buf[name]
  for name in result.keys():
    stats[name].append(result[name]/counter)
  stats["params"].append(params)
  pd.DataFrame(stats).to_csv(stats_dir + str(i) + ".csv")
  print(f"Done {i} out of {len(all_combinations)}")

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name                 | Type              | Params
-----------------------------------------------------------
0 | model                | MySegmentationNet | 12.6 K
1 | loss                 | CrossEntropyLoss  | 0     
2 | val_recal_yellow     | Recall            | 0     
3 | val_precision_yellow | Precision         | 0     
4 | val_recal_white      | Recall            | 0     
5 | val_precision_white  | Precision         | 0     
-----------------------------------------------------------
12.6 K    Trainable params
0         Non-traina

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 0.208


...

Epoch 00005: reducing learning rate of group 0 to 1.0000e-04.


Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Monitored metric val_loss did not improve in the last 5 records. Best score: 0.210. Signaling Trainer to stop.


Done 35 out of 36


In [ ]:
checkpoints_dir = "/content/checkpoints/"# If you use Colab, you can leave this path as it is, otherwise change it, because usually you don't have permissions to create dirs in the root
FaceModuleCheckpoint = ModelCheckpoint(
      dirpath=checkpoints_dir,
      filename="{epoch}-{val_loss:.3f}",
      save_top_k=2,
      mode="min",
      monitor="val_loss",
      every_n_epochs=1,
      save_last=True
  )

MyEarlyStopping = EarlyStopping(monitor="val_loss", mode="min", patience=5, verbose=True)

In [ ]:
# Real training
trainer = pl.Trainer(
      max_epochs=30,
      accelerator="gpu",
      devices=1,
      callbacks=[MyEarlyStopping, FaceModuleCheckpoint],
      log_every_n_steps=50,
  )

training_module = MyTrainingModule(
    opt="adam",
    white_weight=5.0,
    yellow_weight=10.0,
    kernel_size=5,
)

trainer.fit(training_module, dl_train, dl_val)

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name                 | Type              | Params
-----------------------------------------------------------
0 | model                | MySegmentationNet | 12.6 K
1 | loss                 | CrossEntropyLoss  | 0     
2 | val_recal_yellow     | Recall            | 0     
3 | val_precision_yellow | Precision         | 0     
4 | val_recal_white      | Recall            | 0     
5 | val_precision_white  | Precision         | 0     
-----------------------------------------------------------
12.6 K    Trainable params
0         Non-traina

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 0.201


...

Validation: |          | 0/? [00:00<?, ?it/s]

Epoch 00008: reducing learning rate of group 0 to 1.0000e-04.


Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Monitored metric val_loss did not improve in the last 5 records. Best score: 0.161. Signaling Trainer to stop.


In [ ]:
class MyTrainingModuleKernel5(MyTrainingModule):
  def __init__(self,
               opt='adam',
               white_weight=5.0,
               yellow_weight=5.0,
               amount_of_hidden_layers=2,
               kernel_size=5,
               leaky_relu_coef=0,
               dropout=0.3):
    super().__init__(
        opt,
        white_weight,
        yellow_weight,
        amount_of_hidden_layers,
        kernel_size,
        leaky_relu_coef,
        dropout
    )
    self.opt = opt
    self.amount_of_hidden_layers = amount_of_hidden_layers
    self.kernel_size = kernel_size
    self.leaky_relu_coef = leaky_relu_coef
    self.dropout = dropout

    self.model = MySegmentationNet(leaky_relu_coef=leaky_relu_coef, kernel_size=kernel_size, dropout=dropout, block_amount=amount_of_hidden_layers)

class MyTrainingModuleKernel3(MyTrainingModule):
  def __init__(self,
               opt='adam',
               white_weight=5.0,
               yellow_weight=5.0,
               amount_of_hidden_layers=2,
               kernel_size=3,
               leaky_relu_coef=0,
               dropout=0.3):
    super().__init__(
        opt,
        white_weight,
        yellow_weight,
        amount_of_hidden_layers,
        kernel_size,
        leaky_relu_coef,
        dropout
    )
    self.opt = opt
    self.amount_of_hidden_layers = amount_of_hidden_layers
    self.kernel_size = kernel_size
    self.leaky_relu_coef = leaky_relu_coef
    self.dropout = dropout

    self.model = MySegmentationNet(leaky_relu_coef=leaky_relu_coef, kernel_size=kernel_size, dropout=dropout, block_amount=amount_of_hidden_layers)

In [ ]:
tm = MyTrainingModuleKernel5() # Here you have to choose which kernel size to use. If model with kernel_size == 5 was used, use MyTrainingModuleKernel5, otherwise MyTrainingModuleKernel3

In [ ]:
tm = MyTrainingModule.load_from_checkpoint(checkpoints_dir + "epoch=9-val_loss=0.162.ckpt") # You have to change file name to file name with the lowest val_loss in checpoints_dir

In [ ]:
next(tm.model.parameters()).device

device(type='cuda', index=0)

In [ ]:
training_module.model.eval()
next(training_module.model.parameters()).device

device(type='cpu')

In [ ]:
training_module.model.to(torch.device("cpu"))

MySegmentationNet(
  (in_layer): BasicMobileNetBlock(
    (spatial_convolve): Conv2d(3, 3, kernel_size=(5, 5), stride=(1, 1), padding=(2, 2), groups=3, padding_mode=reflect)
    (depthwise_convolve): Conv2d(3, 64, kernel_size=(1, 1), stride=(1, 1))
    (ReLU): ReLU()
    (batch_norm): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (dropout): Dropout2d(p=0.5, inplace=False)
  )
  (basic_layers): Sequential(
    (0): BasicMobileNetBlock(
      (spatial_convolve): Conv2d(64, 64, kernel_size=(5, 5), stride=(1, 1), padding=(2, 2), groups=64, padding_mode=reflect)
      (depthwise_convolve): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1))
      (ReLU): ReLU()
      (batch_norm): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (dropout): Dropout2d(p=0.5, inplace=False)
    )
    (1): BasicMobileNetBlock(
      (spatial_convolve): Conv2d(64, 64, kernel_size=(5, 5), stride=(1, 1), padding=(2, 2), groups=64, padding_mod

In [ ]:
result = {}
counter = 0
model = training_module.model
model.eval()
model.to(device)
training_module.to(device)
with torch.no_grad():
  for data, labels in tqdm(dl_test):
    counter += 1
    data = data.to(device)
    labels = labels.to(device)

    x, y = data, labels

    # y = y / resize_to
    y_pred = model(x)

    y_pred_label = torch.argmax(y_pred, dim=1)
    y_label = y

    loss = training_module.loss(y_pred, y)

    yellow_recal = training_module.val_recal_yellow(y_label, y_pred_label)
    yellow_precision = training_module.val_precision_yellow(y_label, y_pred_label)
    white_recal = training_module.val_recal_white(y_label, y_pred_label)
    white_precision = training_module.val_precision_white(y_label, y_pred_label)

    buf = {
        "val_loss": loss,
        "yellow_recal": yellow_recal,
        "yellow_precision": yellow_precision,
        "white_recal" : white_recal,
        "white_precision" : white_precision,
    }
    del x
    del y
    del y_pred_label
    del y_pred
    del y_label
    if len(result) == 0:
      result = buf
    else:
      for name in result.keys():
        result[name] += buf[name]

  for key in result.keys():
    print(key, result[key] / counter)



  0%|          | 0/53 [00:00<?, ?it/s]

  2%|▏         | 1/53 [00:01<01:14,  1.43s/it]

  4%|▍         | 2/53 [00:01<00:34,  1.46it/s]

  6%|▌         | 3/53 [00:01<00:24,  2.08it/s]

  8%|▊         | 4/53 [00:02<00:19,  2.46it/s]

  9%|▉         | 5/53 [00:02<00:15,  3.10it/s]

 11%|█▏        | 6/53 [00:02<00:14,  3.24it/s]

 13%|█▎        | 7/53 [00:02<00:12,  3.77it/s]

 15%|█▌        | 8/53 [00:03<00:12,  3.57it/s]

 17%|█▋        | 9/53 [00:03<00:10,  4.07it/s]

 19%|█▉        | 10/53 [00:03<00:09,  4.51it/s]

 21%|██        | 11/53 [00:03<00:08,  4.87it/s]

 23%|██▎       | 12/53 [00:03<00:07,  5.16it/s]

 25%|██▍       | 13/53 [00:03<00:07,  5.40it/s]

 26%|██▋       | 14/53 [00:04<00:07,  5.54it/s]

 28%|██▊       | 15/53 [00:04<00:06,  5.44it/s]

 30%|███       | 16/53 [00:04<00:06,  5.71it/s]

 32%|███▏      | 17/53 [00:04<00:06,  5.74it/s]

 34%|███▍      | 18/53 [00:04<00:05,  5.87it/s]

 36%|███▌      | 19/53 [00:04<00:05,  6.00it/s]

 38%|███▊      | 20/53 [00:05<00:05,

In [ ]:
model.to(torch.device("cpu"))

MySegmentationNet(
  (in_layer): BasicMobileNetBlock(
    (spatial_convolve): Conv2d(3, 3, kernel_size=(5, 5), stride=(1, 1), padding=(2, 2), groups=3, padding_mode=reflect)
    (depthwise_convolve): Conv2d(3, 64, kernel_size=(1, 1), stride=(1, 1))
    (ReLU): ReLU()
    (batch_norm): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (dropout): Dropout2d(p=0.5, inplace=False)
  )
  (basic_layers): Sequential(
    (0): BasicMobileNetBlock(
      (spatial_convolve): Conv2d(64, 64, kernel_size=(5, 5), stride=(1, 1), padding=(2, 2), groups=64, padding_mode=reflect)
      (depthwise_convolve): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1))
      (ReLU): ReLU()
      (batch_norm): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (dropout): Dropout2d(p=0.5, inplace=False)
    )
    (1): BasicMobileNetBlock(
      (spatial_convolve): Conv2d(64, 64, kernel_size=(5, 5), stride=(1, 1), padding=(2, 2), groups=64, padding_mod

In [ ]:
torch.save(model.state_dict(), 'model_weights.pth')

If you use Colab, don't forget to download weights to your PC